In [89]:
#import the required packages for linear and polynomial regression
import pandas as pd
import pylab as pl
import numpy as np
import scipy.optimize as opt
import glob

%matplotlib inline
import matplotlib.pyplot as plt

from sklearn import preprocessing
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import confusion_matrix

from sklearn import linear_model
from sklearn.preprocessing import PolynomialFeatures
from sklearn import linear_model

import numpy as np
import sklearn 
import pandas as pd
import matplotlib.pyplot as plt

from utility_code.utility import utils

In [90]:
#Pull the data: 
train_import = pd.read_csv("ucla2020-cs145-covid19-prediction/train.csv")
test_import = pd.read_csv("ucla2020-cs145-covid19-prediction/test.csv")

In [91]:
#use this for linear and poly regression: 
regr = linear_model.LinearRegression()

In [92]:
#array of states
features = ['Confirmed','Deaths']
num_features = len(features)
states = pd.Series.unique(train_import['Province_State'])
num_states = len(states)
states

array(['Alabama', 'Alaska', 'Arizona', 'Arkansas', 'California',
       'Colorado', 'Connecticut', 'Delaware', 'Florida', 'Georgia',
       'Hawaii', 'Idaho', 'Illinois', 'Indiana', 'Iowa', 'Kansas',
       'Kentucky', 'Louisiana', 'Maine', 'Maryland', 'Massachusetts',
       'Michigan', 'Minnesota', 'Mississippi', 'Missouri', 'Montana',
       'Nebraska', 'Nevada', 'New Hampshire', 'New Jersey', 'New Mexico',
       'New York', 'North Carolina', 'North Dakota', 'Ohio', 'Oklahoma',
       'Oregon', 'Pennsylvania', 'Rhode Island', 'South Carolina',
       'South Dakota', 'Tennessee', 'Texas', 'Utah', 'Vermont',
       'Virginia', 'Washington', 'West Virginia', 'Wisconsin', 'Wyoming'],
      dtype=object)

In [93]:
#split training into training and testing
def cut_data(dataframe,percent_split,segment_length=1):
        num_segments = int(dataframe.shape[0] / segment_length)
        num_segment_split1 = int(num_segments * percent_split / 100)
        split1_size = num_segment_split1 * segment_length
        return(dataframe.iloc[:split1_size,:] ,  dataframe.iloc[split1_size:,:])

PERCENT_TRAIN = 80
train , test = cut_data(train_import,PERCENT_TRAIN,num_states)

In [94]:
#stratify by state (into state dictionary)
statesdata = {}
for s in states:
    statesdata[s] = train.loc[train['Province_State'] == s ,features]

#feature name -> column indices
def get_index(dataframe,col_names):
        indices = []
        for c in col_names:
            indices.append(dataframe.columns.get_loc(c))
        return indices


state_feature_indices = get_index(statesdata['California'],features)

In [95]:
#append the feature spaces from the W days prior (where W is the window length)
#set the WINDOW size
size = 10
new_features = []
for day in range(size):
    for f in features:
        new_features.append(f + "(-"+ str(size-day) + " days)")
all_new_features = new_features + features

In [96]:
all_new_features

['Confirmed(-10 days)',
 'Deaths(-10 days)',
 'Confirmed(-9 days)',
 'Deaths(-9 days)',
 'Confirmed(-8 days)',
 'Deaths(-8 days)',
 'Confirmed(-7 days)',
 'Deaths(-7 days)',
 'Confirmed(-6 days)',
 'Deaths(-6 days)',
 'Confirmed(-5 days)',
 'Deaths(-5 days)',
 'Confirmed(-4 days)',
 'Deaths(-4 days)',
 'Confirmed(-3 days)',
 'Deaths(-3 days)',
 'Confirmed(-2 days)',
 'Deaths(-2 days)',
 'Confirmed(-1 days)',
 'Deaths(-1 days)',
 'Confirmed',
 'Deaths']

In [97]:
from itertools import chain

#fill the knn data using days from training set
knndata = pd.DataFrame(columns = all_new_features)
num_training_days = len(statesdata['Alabama'])

def chnage_shape_data(dataframe,row_arg,col_arg):
    return list(chain(*dataframe.iloc[row_arg,col_arg].values.tolist()))
    
def add_row(dataframe,row,s,d):
    row_name = s + " (day " + str(d) + ")"
    dataframe.loc[row_name,:] = row     



#fill the table
for d in range(size,num_training_days):
    for s in states:
        knndata_row_index = knndata.shape[0]
        knn_row = chnage_shape_data(statesdata[s],slice(d-size,d+1), state_feature_indices)
        add_row(knndata,knn_row,s,d)     

In [98]:
knndata

Confirmed(-10 days) Deaths(-10 days)  \
Alabama (day 10)                        3563               93   
Alaska (day 10)                          272                8   
Arizona (day 10)                        3542              115   
Arkansas (day 10)                       1280               27   
California (day 10)                    22795              640   
Colorado (day 10)                       7307              289   
Connecticut (day 10)                   12035              554   
Delaware (day 10)                       1625               35   
Florida (day 10)                       19895              461   
Georgia (day 10)                       12452              433   
Hawaii (day 10)                          499                9   
Idaho (day 10)                          1407               27   
Illinois (day 10)                      20852              720   
Indiana (day 10)                        7928              343   
Iowa (day 10)                           1587               41   
Kansas (day 10)                         1344               56   
Kentucky (day 10)                       1963               97   
Louisiana (day 10)                     20595              840   
Maine (day 10)                           633               19   
Maryland (day 10)                       8225              236   
Massachusetts (day 10)                 25475              756   
Michigan (day 10)                      24244             1479   
Minnesota (day 10)                      1621               70   
Mississippi (day 10)                    2781               96   
Missouri (day 10)                       4269              118   
Montana (day 10)                         387                6   
Nebraska (day 10)                        791               17   
Nevada (day 10)                         2836              112   
New Hampshire (day 10)                   929               23   
New Jersey (day 10)                    61850             2350   
New Mexico (day 10)                     1245               26   
New York (day 10)                     189033             9385   
North Carolina (day 10)                 4570               89   
North Dakota (day 10)                    308                7   
Ohio (day 10)                           6604              253   
Oklahoma (day 10)                       1970               96   
Oregon (day 10)                         1527               52   
Pennsylvania (day 10)                  22938              557   
Rhode Island (day 10)                   2665               63   
South Carolina (day 10)                 3320               82   
South Dakota (day 10)                    730                6   
Tennessee (day 10)                      5508              106   
Texas (day 10)                         13677              283   
Utah (day 10)                           2303               18   
Vermont (day 10)                         727               27   
Virginia (day 10)                       5274              141   
Washington (day 10)                    10609              506   
West Virginia (day 10)                   593                6   
Wisconsin (day 10)                      3341              144   
Wyoming (day 10)                         270                0   
Alabama (day 11)                        3734               99   
Alaska (day 11)                          277                8   
Arizona (day 11)                        3705              122   
Arkansas (day 11)                       1410               29   
California (day 11)                    23931              714   
Colorado (day 11)                       7691              306   
Connecticut (day 11)                   13381              602   
Delaware (day 11)                       1758               41   
Florida (day 11)                       21019              499   
Georgia (day 11)                       13315              465   
Hawaii (day 11)                          504                

In [108]:
knndata.shape

(5150, 22)

In [99]:
ff = knndata.iloc[0]

In [100]:
#knndata.columns.values
train_x = np.asanyarray(knndata[['Confirmed(-10 days)', 'Deaths(-10 days)', 'Confirmed(-9 days)',
       'Deaths(-9 days)', 'Confirmed(-8 days)', 'Deaths(-8 days)',
       'Confirmed(-7 days)', 'Deaths(-7 days)', 'Confirmed(-6 days)',
       'Deaths(-6 days)', 'Confirmed(-5 days)', 'Deaths(-5 days)',
       'Confirmed(-4 days)', 'Deaths(-4 days)', 'Confirmed(-3 days)',
       'Deaths(-3 days)', 'Confirmed(-2 days)', 'Deaths(-2 days)',
       'Confirmed(-1 days)', 'Deaths(-1 days)']])
train_y = np.asanyarray(knndata[['Confirmed', 'Deaths']])

In [101]:
regr.fit (train_x, train_y)

LinearRegression()

In [102]:
#Make test Cases: 
test_x = np.asanyarray(ff[['Confirmed(-10 days)', 'Deaths(-10 days)', 'Confirmed(-9 days)',
       'Deaths(-9 days)', 'Confirmed(-8 days)', 'Deaths(-8 days)',
       'Confirmed(-7 days)', 'Deaths(-7 days)', 'Confirmed(-6 days)',
       'Deaths(-6 days)', 'Confirmed(-5 days)', 'Deaths(-5 days)',
       'Confirmed(-4 days)', 'Deaths(-4 days)', 'Confirmed(-3 days)',
       'Deaths(-3 days)', 'Confirmed(-2 days)', 'Deaths(-2 days)',
       'Confirmed(-1 days)', 'Deaths(-1 days)']])

test_y = np.asanyarray(ff[['Confirmed', 'Deaths']])

In [103]:
test_x = test_x.reshape(1, -1)
y_prediction = regr.predict(test_x)

In [104]:
y_prediction 

array([[5573.02092354,  190.94980051]])

In [105]:
test_y = test_y.reshape(1, -1)

In [106]:
test_y

array([[5593, 196]], dtype=object)

In [107]:
from sklearn.metrics import mean_absolute_error
mean_absolute_error(test_y, y_prediction)

12.514637975792468

In [112]:
last_ten_august = knndata.iloc[-500:]
last_ten_august

Confirmed(-10 days) Deaths(-10 days)  \
Alabama (day 103)                      57255             1164   
Alaska (day 103)                        1579               17   
Arizona (day 103)                     128097             2337   
Arkansas (day 103)                     29812              331   
California (day 103)                  346211             7250   
Colorado (day 103)                     37668             1738   
Connecticut (day 103)                  47530             4372   
Delaware (day 103)                     12969              518   
Florida (day 103)                     291629             4409   
Georgia (day 103)                     123963             3054   
Hawaii (day 103)                        1264               22   
Idaho (day 103)                        11720              103   
Illinois (day 103)                    156638             7419   
Indiana (day 103)                      52685             2775   
Iowa (day 103)                         35866              757   
Kansas (day 103)                       19887              299   
Kentucky (day 103)                     20223              635   
Louisiana (day 103)                    82042             3445   
Maine (day 103)                         3566              114   
Maryland (day 103)                     74260             3334   
Massachusetts (day 103)               112130             8340   
Michigan (day 103)                     77864             6326   
Minnesota (day 103)                    43170             1548   
Mississippi (day 103)                  37542             1272   
Missouri (day 103)                     29240             1114   
Montana (day 103)                       1952               34   
Nebraska (day 103)                     21717              286   
Nevada (day 103)                       29619              612   
New Hampshire (day 103)                 6091              392   
New Jersey (day 103)                  175915            15582   
New Mexico (day 103)                   15514              551   
New York (day 103)                    403175            32408   
North Carolina (day 103)               90000             1571   
North Dakota (day 103)                  4493               88   
Ohio (day 103)                         67995             3069   
Oklahoma (day 103)                     21740              428   
Oregon (day 103)                       12805              244   
Pennsylvania (day 103)                101266             6931   
Rhode Island (day 103)                 17588              985   
South Carolina (day 103)               60389              993   
South Dakota (day 103)                  7572              109   
Tennessee (day 103)                    66788              767   
Texas (day 103)                       279577             3362   
Utah (day 103)                         30478              226   
Vermont (day 103)                       1305               56   
Virginia (day 103)                     72443             1977   
Washington (day 103)                   42304             1404   
West Virginia (day 103)                 4407               97   
Wisconsin (day 103)                    37906              826   
Wyoming (day 103)                       1950               22   
Alabama (day 104)                      59067             1211   
Alaska (day 104)                        1631               17   
Arizona (day 104)                     131354             2434   
Arkansas (day 104)                     30297              335   
California (day 104)                  354885             7375   
Colorado (day 104)                     38137             1744   
Connecticut (day 104)                  47636             4380   
Delaware (day 104)                     13050              521   
Florida (day 104)                     301810             4521   
Georgia (day 104)                     127838             3091   
Hawaii (day 104)                        1292               2